<h1 style="color:red;"> Capstone Project: Battle of Neighborhoods</h1>

### Table of Contents

<div class="alert alert-block alert-info" style="margin-top: 20px">
<ol>
    <li><a href="#1.-Introduction---Business-Problem">Introduction - Business Problem</a>        
    <li><a href="#2.Data Preparation">Data</a>
        <ul>Toronto Neighborhood Data</ul>
        <ul>Building the Yoga Venues data using Foursquare API</ul>
        <ul>Data visualization</ul>
        <ul>Venues surrounding yoga studios in Toronto</ul>
    <li><a href="#3.-Data-Analysis">Data Analysis</a>
        <ul>Examine Clusters</ul>
    <li><a href="#4.-Results">Results</a>
</ol>
</div>

<h2 style="color:blue;">1. <u>Introduction - Business Problem</u> </h2>
<h3>Opening a Yoga Studio</h3>

<i>I want to open a new Yoga Studio in Toronto. Where should I open it? </i>
This is one of the questions that an entrepreneur would need to answer before starting his or her yoga studio. Location is key for a new business and one that requires careful research. In this capstone project, I will attempt to solve this problem through data analysis.

<h2 style="color:blue;">2.<u>Data Preparation</u></h2>

To solve the problem, we will need the following data : 
<ul>
    <li><b>Toronto Neighborhood data</b> which we already have from previous assignments
    <li><b>Foursquare yoga venues data</b>: for each neighborhood, we will be running an API call to pull all the yoga venues within 5km of the geographical coordinates provided in the Toronto Neighborhood data</li>
    <li><b>Foursquare nearby venues data</b> we will need to pull the venues that surrounds the yoga venue for pattern analysis</li>
  

### Toronto Neighborhood Data 
In this section we will be building the Neighborhood data profile which consists of the Neighborhood name, Borough name, Postal Code, Latitude and Longitude

In [1]:
import pandas as pd
import numpy as np
import wget
import requests
import csv
import geocoder
import geopy
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
import folium
import json 
import matplotlib.pyplot as plt
print("Libraries imported")

Libraries imported


#### Data Cleaning and Wrangling

We will use the data from the previous assignment to retrieve the zip codes and then the geolocation data for each neighborhood. We will not use Borough in this section

In [2]:
#let's open the csv file
csvfile = "C:/Users/nirin/Downloads/output.csv"
neighpostal = pd.read_csv(csvfile,
                 header=0,
                 delimiter='  ',                 
                 quotechar='"',
                 error_bad_lines=False,
                 engine='python')
neighpostal.shape

(180, 3)

In [3]:
neighpostal.drop(neighpostal[neighpostal['Borough'] =='Not assigned'].index, inplace = True)
print("removed rows with Not assigned Borough")

removed rows with Not assigned Borough


In [4]:
neighpostal.shape

(103, 3)

Next we will need to pull the Latitude and Longitude data which are stored in the Geospatial coordinates file

In [5]:
#Importing the geographical data
geodf = pd.read_csv("C:/Users/nirin/Geospatial_Coordinates.csv",                   
                 header=0,
                 delimiter=",",                 
                 error_bad_lines=False,
                 engine='python'
                   )
geodf.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

Now let's merge the two dataframe to obtain the desired data

In [6]:
dfmerge = neighpostal.merge(geodf)
dfmerge.rename(columns = {'Neighbourhood' : 'Neighborhood' }, inplace = True)
dfmerge.tail(5)

Postal Code           Borough  \
98          M8X         Etobicoke   
99          M4Y  Downtown Toronto   
100         M7Y      East Toronto   
101         M8Y         Etobicoke   
102         M8Z         Etobicoke   

                                          Neighborhood   Latitude  Longitude  
98   The Kingsway,Montgomery Road,Old Mill North,Ki...  43.653654 -79.506944  
99                                Church and Wellesley  43.665860 -79.383160  
100  Business reply mail Processing Centre,South Ce...  43.662744 -79.321558  
101  Old Mill South,King's Mill Park,Sunnylea,Humbe...  43.636258 -79.498509  
102  Mimico NW,The Queensway West,South of Bloor,Ki...  43.628841 -79.520999

It looks like the data is still grouped by Borough, let's change it so that each unique Neighbourhood is in it's own row

In [7]:
dfmerge['Neighborhood'] = dfmerge['Neighborhood'].str.split(',')

In [8]:
dfmerge = dfmerge.explode('Neighborhood')
dfmerge.shape

(304, 5)

In [47]:
dfmerge.head(6)

Postal Code           Borough       Neighborhood   Latitude  Longitude
0         M3A        North York          Parkwoods  43.753259 -79.329656
0         M3A        North York  Parkwoods-Donalda  43.753259 -79.329656
1         M4A        North York   Victoria Village  43.725882 -79.315572
2         M5A  Downtown Toronto        Regent Park  43.654260 -79.360636
2         M5A  Downtown Toronto       Harbourfront  43.654260 -79.360636
2         M5A  Downtown Toronto          Moss Park  43.654260 -79.360636

We have our first dataframe!

## Building the Yoga Venues data using Foursquare API

In this section, let's use the Foursquare API to get a list of the yoga studios around toronto for each neighborhood

In [9]:
import random # library for random number generation
from geopy.geocoders import Nominatim # module to convert an address into latitude and longitude values

# libraries for displaying images
from IPython.display import Image 
from IPython.core.display import HTML 
    
# tranforming json file into a pandas dataframe library
from pandas.io.json import json_normalize

In [10]:
CLIENT_ID = 'NGBR4FWG0IAT0DHXIBKYXI2E1JI2LEJMEL3L1YA1RW4CSLXG'
CLIENT_SECRET = '23BDE00ECXWL0IEIDFLXDMQIK0PERQTG1MSKSKUOGBPAQSRJ' 
VERSION = '20180323'
#VERSION = '20190425'
LIMIT = 20
print('My credentials:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

My credentials:
CLIENT_ID: NGBR4FWG0IAT0DHXIBKYXI2E1JI2LEJMEL3L1YA1RW4CSLXG
CLIENT_SECRET:23BDE00ECXWL0IEIDFLXDMQIK0PERQTG1MSKSKUOGBPAQSRJ


In [11]:
query = 'yoga class'
radius = 500
neighb = 'Annex'
geolocator = Nominatim(user_agent="foursquare_agent")
location = geolocator.geocode(neighb)
latitude = location.latitude
longitude = location.longitude
print(latitude, longitude)

43.6703377 -79.407117


Let's create a function that iterates through all the neighborhood and runs an API call against each row in the dataframe

In [15]:
def getYogaStudios(names, latitudes, longitudes, radius=5000):
    
    venues_list = []
    
    for name, lat, lng in zip(names, latitudes, longitudes):     
                
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&query=yoga class&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
          
        # make the GET request        
        results = requests.get(url).json()['response']['groups'][0]['items']
        print(results)                
            
            
        # return only relevant information for each nearby venue    
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng']) for v in results])
        
        #Create the dataframe
    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude']
    print("Dataframe Created")    
    return(nearby_venues)

In [16]:
query_results = getYogaStudios(names = dfmerge['Neighborhood'],
                                  latitudes = dfmerge['Latitude'],
                                   longitudes = dfmerge['Longitude']
                                  )

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4c18e819d4d9c9284e19f029', 'name': 'LA Fitness', 'contact': {}, 'location': {'address': '1380 Don Mills Road', 'crossStreet': 'Mallard Rd', 'lat': 43.74766522888878, 'lng': -79.34707696065234, 'labeledLatLngs': [{'label': 'display', 'lat': 43.74766522888878, 'lng': -79.34707696065234}], 'distance': 1532, 'postalCode': 'M3B 2X2', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['1380 Don Mills Road (Mallard Rd)', 'Toronto ON M3B 2X2', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d176941735', 'name': 'Gym', 'pluralName': 'Gyms', 'shortName': 'Gym', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/building/gym_', 'suffix': '.png'}, 'primary': True}], 'verified': True, 'stats': {'tipCount': 0, 'usersCount': 0, 'checkinsCount': 0, 'visitsCount': 0}, 'beenHere': {'count': 0, 'lastCheckinExp

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '50bf6e53d86ce1965377956b', 'name': 'Y Yoga', 'contact': {}, 'location': {'address': '204 - 350 Queens Quay West', 'crossStreet': 'Between Spadina and Rees St.', 'lat': 43.638533613620204, 'lng': -79.38915754933562, 'labeledLatLngs': [{'label': 'display', 'lat': 43.638533613620204, 'lng': -79.38915754933562}], 'distance': 2888, 'postalCode': 'M5V 3A7', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['204 - 350 Queens Quay West (Between Spadina and Rees St.)', 'Toronto ON M5V 3A7', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d102941735', 'name': 'Yoga Studio', 'pluralName': 'Yoga Studios', 'shortName': 'Yoga Studio', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/gym_yogastudio_', 'suffix': '.png'}, 'primary': True}], 'verified': False, 'stats': {'tipCount': 0, 'usersCount': 0

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '50bf6e53d86ce1965377956b', 'name': 'Y Yoga', 'contact': {}, 'location': {'address': '204 - 350 Queens Quay West', 'crossStreet': 'Between Spadina and Rees St.', 'lat': 43.638533613620204, 'lng': -79.38915754933562, 'labeledLatLngs': [{'label': 'display', 'lat': 43.638533613620204, 'lng': -79.38915754933562}], 'distance': 2888, 'postalCode': 'M5V 3A7', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['204 - 350 Queens Quay West (Between Spadina and Rees St.)', 'Toronto ON M5V 3A7', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d102941735', 'name': 'Yoga Studio', 'pluralName': 'Yoga Studios', 'shortName': 'Yoga Studio', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/gym_yogastudio_', 'suffix': '.png'}, 'primary': True}], 'verified': False, 'stats': {'tipCount': 0, 'usersCount': 0

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '50bf6e53d86ce1965377956b', 'name': 'Y Yoga', 'contact': {}, 'location': {'address': '204 - 350 Queens Quay West', 'crossStreet': 'Between Spadina and Rees St.', 'lat': 43.638533613620204, 'lng': -79.38915754933562, 'labeledLatLngs': [{'label': 'display', 'lat': 43.638533613620204, 'lng': -79.38915754933562}], 'distance': 2888, 'postalCode': 'M5V 3A7', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['204 - 350 Queens Quay West (Between Spadina and Rees St.)', 'Toronto ON M5V 3A7', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d102941735', 'name': 'Yoga Studio', 'pluralName': 'Yoga Studios', 'shortName': 'Yoga Studio', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/gym_yogastudio_', 'suffix': '.png'}, 'primary': True}], 'verified': False, 'stats': {'tipCount': 0, 'usersCount': 0

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '50bf6e53d86ce1965377956b', 'name': 'Y Yoga', 'contact': {}, 'location': {'address': '204 - 350 Queens Quay West', 'crossStreet': 'Between Spadina and Rees St.', 'lat': 43.638533613620204, 'lng': -79.38915754933562, 'labeledLatLngs': [{'label': 'display', 'lat': 43.638533613620204, 'lng': -79.38915754933562}], 'distance': 2888, 'postalCode': 'M5V 3A7', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['204 - 350 Queens Quay West (Between Spadina and Rees St.)', 'Toronto ON M5V 3A7', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d102941735', 'name': 'Yoga Studio', 'pluralName': 'Yoga Studios', 'shortName': 'Yoga Studio', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/gym_yogastudio_', 'suffix': '.png'}, 'primary': True}], 'verified': False, 'stats': {'tipCount': 0, 'usersCount': 0

...

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '53669066498eb02e34d50dcd', 'name': 'Yoga Grove - Small Classes. Big Difference.', 'contact': {}, 'location': {'address': '23 Wendover Road', 'crossStreet': 'Prince Edward and Bloor', 'lat': 43.64922739104706, 'lng': -79.50681209564209, 'labeledLatLngs': [{'label': 'display', 'lat': 43.64922739104706, 'lng': -79.50681209564209}], 'distance': 2540, 'postalCode': 'M8X 2L1', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['23 Wendover Road (Prince Edward and Bloor)', 'Toronto ON M8X 2L1', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d102941735', 'name': 'Yoga Studio', 'pluralName': 'Yoga Studios', 'shortName': 'Yoga Studio', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/gym_yogastudio_', 'suffix': '.png'}, 'primary': True}], 'verified': True, 'stats': {'tipCount': 0, 'usersCount

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '53669066498eb02e34d50dcd', 'name': 'Yoga Grove - Small Classes. Big Difference.', 'contact': {}, 'location': {'address': '23 Wendover Road', 'crossStreet': 'Prince Edward and Bloor', 'lat': 43.64922739104706, 'lng': -79.50681209564209, 'labeledLatLngs': [{'label': 'display', 'lat': 43.64922739104706, 'lng': -79.50681209564209}], 'distance': 2540, 'postalCode': 'M8X 2L1', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['23 Wendover Road (Prince Edward and Bloor)', 'Toronto ON M8X 2L1', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d102941735', 'name': 'Yoga Studio', 'pluralName': 'Yoga Studios', 'shortName': 'Yoga Studio', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/gym_yogastudio_', 'suffix': '.png'}, 'primary': True}], 'verified': True, 'stats': {'tipCount': 0, 'usersCount

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '53669066498eb02e34d50dcd', 'name': 'Yoga Grove - Small Classes. Big Difference.', 'contact': {}, 'location': {'address': '23 Wendover Road', 'crossStreet': 'Prince Edward and Bloor', 'lat': 43.64922739104706, 'lng': -79.50681209564209, 'labeledLatLngs': [{'label': 'display', 'lat': 43.64922739104706, 'lng': -79.50681209564209}], 'distance': 2540, 'postalCode': 'M8X 2L1', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['23 Wendover Road (Prince Edward and Bloor)', 'Toronto ON M8X 2L1', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d102941735', 'name': 'Yoga Studio', 'pluralName': 'Yoga Studios', 'shortName': 'Yoga Studio', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/gym_yogastudio_', 'suffix': '.png'}, 'primary': True}], 'verified': True, 'stats': {'tipCount': 0, 'usersCount

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '53669066498eb02e34d50dcd', 'name': 'Yoga Grove - Small Classes. Big Difference.', 'contact': {}, 'location': {'address': '23 Wendover Road', 'crossStreet': 'Prince Edward and Bloor', 'lat': 43.64922739104706, 'lng': -79.50681209564209, 'labeledLatLngs': [{'label': 'display', 'lat': 43.64922739104706, 'lng': -79.50681209564209}], 'distance': 2540, 'postalCode': 'M8X 2L1', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['23 Wendover Road (Prince Edward and Bloor)', 'Toronto ON M8X 2L1', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d102941735', 'name': 'Yoga Studio', 'pluralName': 'Yoga Studios', 'shortName': 'Yoga Studio', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/gym_yogastudio_', 'suffix': '.png'}, 'primary': True}], 'verified': True, 'stats': {'tipCount': 0, 'usersCount

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '53669066498eb02e34d50dcd', 'name': 'Yoga Grove - Small Classes. Big Difference.', 'contact': {}, 'location': {'address': '23 Wendover Road', 'crossStreet': 'Prince Edward and Bloor', 'lat': 43.64922739104706, 'lng': -79.50681209564209, 'labeledLatLngs': [{'label': 'display', 'lat': 43.64922739104706, 'lng': -79.50681209564209}], 'distance': 2540, 'postalCode': 'M8X 2L1', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['23 Wendover Road (Prince Edward and Bloor)', 'Toronto ON M8X 2L1', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d102941735', 'name': 'Yoga Studio', 'pluralName': 'Yoga Studios', 'shortName': 'Yoga Studio', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/gym_yogastudio_', 'suffix': '.png'}, 'primary': True}], 'verified': True, 'stats': {'tipCount': 0, 'usersCount

In [18]:
query_results.reset_index(drop=True, inplace = True)

In [48]:
query_results.shape

(2138, 6)

In [20]:
yogastudios = query_results.drop_duplicates(subset=['Venue', 'Venue Latitude','Venue Longitude'], keep='first', inplace=False)

In [21]:
yogastudios.reset_index(drop = True)
yogastudios.shape

(62, 6)

Now that we have all of our data. let's explore the results

### Data visualization: all the yoga studios on a map

In [22]:
# create map of Manhattan using latitude and longitude values
map_yoga = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(yogastudios['Venue Latitude'], yogastudios['Venue Longitude'], yogastudios['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_yoga)  
    
map_yoga

### Let's get a count by neighborhood

In [23]:
countbyneigh = yogastudios.groupby(['Neighborhood']).size().reset_index(name='counts')
countbyneigh = countbyneigh.sort_values(['counts'], ascending = False,ignore_index=True, key=None)
countbyneigh.head()

Neighborhood  counts
0        Regent Park      15
1          Glencairn       6
2  Hillcrest Village       5
3   Islington Avenue       5
4   Woodbine Heights       3

It appears that Regent Park is the neighborhood with the most # of yoga studios

## Venues surrounding yoga studios in Toronto

Let's create a function that finds nearby venues

In [24]:
def getNearbyVenues(neighborhood, names, latitudes, longitudes, radius=200):
    
    venues_list = []
    
    for neighb, name, lat, lng in zip(neighborhood, names, latitudes, longitudes):     
                
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
          
        # make the GET request
        
        results = requests.get(url).json()['response']['groups'][0]['items']
        print(results)                
            
            
        # return only relevant information for each nearby venue
        #if not 
        venues_list.append([(
            neighb,
            name, 
            lat, 
            lng,            
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],
            v['venue']['categories'][0]['shortName']) for v in results])
        
        #Create the dataframe
    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood','Yoga Place', 
                  'Yoga Place Latitude', 
                  'Yoga Place Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude',
                  'Venue Category']
    print("Dataframe Created")    
    return(nearby_venues)

Let's use our function on the yogastudios dataframe

In [25]:
surrounding_venues = getNearbyVenues(neighborhood = yogastudios['Neighborhood'],
                                     names = yogastudios['Venue'] , 
                                     latitudes = yogastudios['Venue Latitude'], 
                                     longitudes = yogastudios['Venue Longitude'])

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4c18e819d4d9c9284e19f029', 'name': 'LA Fitness', 'contact': {}, 'location': {'address': '1380 Don Mills Road', 'crossStreet': 'Mallard Rd', 'lat': 43.74766522888878, 'lng': -79.34707696065234, 'labeledLatLngs': [{'label': 'display', 'lat': 43.74766522888878, 'lng': -79.34707696065234}], 'distance': 0, 'postalCode': 'M3B 2X2', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['1380 Don Mills Road (Mallard Rd)', 'Toronto ON M3B 2X2', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d176941735', 'name': 'Gym', 'pluralName': 'Gyms', 'shortName': 'Gym', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/building/gym_', 'suffix': '.png'}, 'primary': True}], 'verified': True, 'stats': {'tipCount': 0, 'usersCount': 0, 'checkinsCount': 0, 'visitsCount': 0}, 'beenHere': {'count': 0, 'lastCheckinExpire

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4daf08e66e81e2dffdd4fe40', 'name': 'Iqbal Kebab & Sweet Centre', 'contact': {}, 'location': {'address': '2 Thorncliffe Park Drive, Unit #17', 'lat': 43.705923230061344, 'lng': -79.35152127765924, 'labeledLatLngs': [{'label': 'display', 'lat': 43.705923230061344, 'lng': -79.35152127765924}], 'distance': 53, 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['2 Thorncliffe Park Drive, Unit #17', 'Toronto ON', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d10f941735', 'name': 'Indian Restaurant', 'pluralName': 'Indian Restaurants', 'shortName': 'Indian', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/indian_', 'suffix': '.png'}, 'primary': True}], 'verified': False, 'stats': {'tipCount': 0, 'usersCount': 0, 'checkinsCount': 0, 'visitsCount': 0}, 'beenHere': {'count': 0, 'lastCheckinE

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4b618500f964a52090162ae3', 'name': 'HTO Park', 'contact': {}, 'location': {'address': "Queen's Quay", 'crossStreet': 'at Rees St.', 'lat': 43.63794857171933, 'lng': -79.38781965601113, 'labeledLatLngs': [{'label': 'display', 'lat': 43.63794857171933, 'lng': -79.38781965601113}], 'distance': 125, 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ["Queen's Quay (at Rees St.)", 'Toronto ON', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d163941735', 'name': 'Park', 'pluralName': 'Parks', 'shortName': 'Park', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/parks_outdoors/park_', 'suffix': '.png'}, 'primary': True}], 'verified': False, 'stats': {'tipCount': 0, 'usersCount': 0, 'checkinsCount': 0, 'visitsCount': 0}, 'beenHere': {'count': 0, 'lastCheckinExpiredAt': 0, 'marked': False, 'unconfi

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4aeb5989f964a5203ec121e3', 'name': 'The Yoga Sanctuary', 'contact': {}, 'location': {'address': '2 College St. W, Suite 306', 'crossStreet': 'at Yonge St.', 'lat': 43.661499497597596, 'lng': -79.38363613350754, 'labeledLatLngs': [{'label': 'display', 'lat': 43.661499497597596, 'lng': -79.38363613350754}], 'distance': 0, 'postalCode': 'M5G 1K3', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['2 College St. W, Suite 306 (at Yonge St.)', 'Toronto ON M5G 1K3', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d102941735', 'name': 'Yoga Studio', 'pluralName': 'Yoga Studios', 'shortName': 'Yoga Studio', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/gym_yogastudio_', 'suffix': '.png'}, 'primary': True}], 'verified': True, 'stats': {'tipCount': 0, 'usersCount': 0, 'checkinsCount': 0, 'v

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4fcb97f7e4b00a0e8520b055', 'name': 'Hogtown Smoke', 'contact': {}, 'location': {'address': '1959 Queen St E', 'lat': 43.64928693557788, 'lng': -79.37468932637938, 'labeledLatLngs': [{'label': 'display', 'lat': 43.64928693557788, 'lng': -79.37468932637938}], 'distance': 44, 'postalCode': 'M4L 1H7', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['1959 Queen St E', 'Toronto ON M4L 1H7', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d1cb941735', 'name': 'Food Truck', 'pluralName': 'Food Trucks', 'shortName': 'Food Truck', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/streetfood_', 'suffix': '.png'}, 'primary': True}], 'verified': True, 'stats': {'tipCount': 0, 'usersCount': 0, 'checkinsCount': 0, 'visitsCount': 0}, 'beenHere': {'count': 0, 'lastCheckinExpiredAt': 0, 'marked': Fal

...

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4b91740af964a520adbd33e3', 'name': 'Coffee Tree Roastery', 'contact': {}, 'location': {'address': '2412 Bloor Street West', 'lat': 43.64964735112305, 'lng': -79.48343639040918, 'labeledLatLngs': [{'label': 'display', 'lat': 43.64964735112305, 'lng': -79.48343639040918}], 'distance': 182, 'postalCode': 'M6S 1P9', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['2412 Bloor Street West', 'Toronto ON M6S 1P9', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d16d941735', 'name': 'Café', 'pluralName': 'Cafés', 'shortName': 'Café', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/cafe_', 'suffix': '.png'}, 'primary': True}], 'verified': False, 'stats': {'tipCount': 0, 'usersCount': 0, 'checkinsCount': 0, 'visitsCount': 0}, 'beenHere': {'count': 0, 'lastCheckinExpiredAt': 0, 'marked': Fals

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4b6efbf8f964a520c1d42ce3', 'name': 'Concord Food Centre', 'contact': {}, 'location': {'address': '1438 Centre Street', 'crossStreet': 'Dufferin', 'lat': 43.80647581743824, 'lng': -79.47271404370676, 'labeledLatLngs': [{'label': 'display', 'lat': 43.80647581743824, 'lng': -79.47271404370676}], 'distance': 90, 'postalCode': 'L4J 3N1', 'cc': 'CA', 'city': 'Thornhill', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['1438 Centre Street (Dufferin)', 'Thornhill ON L4J 3N1', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d118951735', 'name': 'Grocery Store', 'pluralName': 'Grocery Stores', 'shortName': 'Grocery Store', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/food_grocery_', 'suffix': '.png'}, 'primary': True}], 'verified': False, 'stats': {'tipCount': 0, 'usersCount': 0, 'checkinsCount': 0, 'visitsCount': 0}

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4c3f7c81da3dc928c9f2c5b9', 'name': 'Gardiner Expy at Park Lawn', 'contact': {}, 'location': {'address': 'Gardiner Expressway', 'crossStreet': 'at Park Lawn Rd.', 'lat': 43.62600539769414, 'lng': -79.48692412832374, 'labeledLatLngs': [{'label': 'display', 'lat': 43.62600539769414, 'lng': -79.48692412832374}], 'distance': 148, 'cc': 'CA', 'neighborhood': 'Humber Bay', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['Gardiner Expressway (at Park Lawn Rd.)', 'Toronto ON', 'Canada']}, 'categories': [{'id': '52f2ab2ebcbc57f1066b8b4c', 'name': 'Intersection', 'pluralName': 'Intersections', 'shortName': 'Intersection', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/travel/default_', 'suffix': '.png'}, 'primary': True}], 'verified': False, 'stats': {'tipCount': 0, 'usersCount': 0, 'checkinsCount': 0, 'visi

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '54f778ee498ed2f9927ca692', 'name': "Longo's", 'contact': {}, 'location': {'address': '1125 North Service Rd', 'crossStreet': 'Stansfield', 'lat': 43.59241587967815, 'lng': -79.57446335230044, 'labeledLatLngs': [{'label': 'display', 'lat': 43.59241587967815, 'lng': -79.57446335230044}], 'distance': 155, 'postalCode': 'L4Y 1A6', 'cc': 'CA', 'city': 'Mississauga', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['1125 North Service Rd (Stansfield)', 'Mississauga ON L4Y 1A6', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d118951735', 'name': 'Grocery Store', 'pluralName': 'Grocery Stores', 'shortName': 'Grocery Store', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/food_grocery_', 'suffix': '.png'}, 'primary': True}], 'verified': False, 'stats': {'tipCount': 0, 'usersCount': 0, 'checkinsCount': 0, 'visitsCount':

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '5a2d984cc6666601b62748f4', 'name': 'Air Canada Signature Suite', 'contact': {}, 'location': {'address': 'Terminal 1, Concourse E', 'crossStreet': 'Toronto Pearson International Airport', 'lat': 43.676704557733416, 'lng': -79.61103533569258, 'labeledLatLngs': [{'label': 'display', 'lat': 43.676704557733416, 'lng': -79.61103533569258}], 'distance': 91, 'postalCode': 'L5P', 'cc': 'CA', 'city': 'Mississauga', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['Terminal 1, Concourse E (Toronto Pearson International Airport)', 'Mississauga ON L5P', 'Canada']}, 'categories': [{'id': '4eb1bc533b7b2c5b1d4306cb', 'name': 'Airport Lounge', 'pluralName': 'Airport Lounges', 'shortName': 'Lounge', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/nightlife/default_', 'suffix': '.png'}, 'primary': True}], 'verified': False, 'stats': {'t

In [50]:
surrounding_venues.head()

Neighborhood       Yoga Place  Yoga Place Latitude  Yoga Place Longitude  \
0    Parkwoods       LA Fitness            43.747665            -79.347077   
1    Parkwoods       LA Fitness            43.747665            -79.347077   
2    Parkwoods       LA Fitness            43.747665            -79.347077   
3    Parkwoods       LA Fitness            43.747665            -79.347077   
4    Parkwoods  Breathe in Yoga            43.777095            -79.348193   

                       Venue  Venue Latitude  Venue Longitude   Venue Category  
0                 LA Fitness       43.747665       -79.347077              Gym  
1                     Subway       43.748423       -79.347207       Sandwiches  
2  the REALTOR® Store @ TREB       43.749428       -79.347339  Office Supplies  
3           Wooffles & Cream       43.748159       -79.348235         Desserts  
4             Tommy Hilfiger       43.777427       -79.345893          Apparel

In [27]:
#We need to drop the venues that are tagged as Yoga Studio
surrounding_venues = surrounding_venues.drop(surrounding_venues[(surrounding_venues["Venue Category"] == 'Yoga Studio')].index)
surrounding_venues.head()

Neighborhood       Yoga Place  Yoga Place Latitude  Yoga Place Longitude  \
0    Parkwoods       LA Fitness            43.747665            -79.347077   
1    Parkwoods       LA Fitness            43.747665            -79.347077   
2    Parkwoods       LA Fitness            43.747665            -79.347077   
3    Parkwoods       LA Fitness            43.747665            -79.347077   
4    Parkwoods  Breathe in Yoga            43.777095            -79.348193   

                       Venue  Venue Latitude  Venue Longitude   Venue Category  
0                 LA Fitness       43.747665       -79.347077              Gym  
1                     Subway       43.748423       -79.347207       Sandwiches  
2  the REALTOR® Store @ TREB       43.749428       -79.347339  Office Supplies  
3           Wooffles & Cream       43.748159       -79.348235         Desserts  
4             Tommy Hilfiger       43.777427       -79.345893          Apparel

Now for each Neighborhood, let's count each unique Venue Category and store it in a new dataframe called around_yoga. 

In [28]:
around_yoga = surrounding_venues.groupby(['Neighborhood','Venue Category']).size().reset_index(name='Category Count')
around_yoga.head()

Neighborhood  Venue Category  Category Count
0    Alderwood            Bank               2
1    Alderwood     Coffee Shop               2
2    Alderwood  Discount Store               2
3    Alderwood   Grocery Store               2
4    Alderwood       Ice Cream               2

Let's sort the data based on the Category Count from highest to lowest

In [29]:
sorted_aroundyoga = around_yoga.sort_values('Category Count',ascending=False, ignore_index=True, key=None)
sorted_aroundyoga.head(5)

Neighborhood      Venue Category  Category Count
0       Regent Park         Coffee Shop              13
1         Glencairn         Coffee Shop              10
2       Regent Park          Sandwiches              10
3  Islington Avenue         Coffee Shop               9
4       Regent Park  Vegetarian / Vegan               7

So far we have good insight but let's add the total count of Yoga Venues per neighborhood to the Venue Grouping data

In [56]:
yoga_cumul = sorted_aroundyoga.merge(countbyneigh)
yoga_cumul.head()

Neighborhood      Venue Category  Category Count  counts
0  Regent Park         Coffee Shop              13      15
1  Regent Park          Sandwiches              10      15
2  Regent Park  Vegetarian / Vegan               7      15
3  Regent Park                Café               7      15
4  Regent Park             Apparel               6      15

In [58]:
yoga_cumul.rename(columns = {'counts' : '#Yoga Venues'}, inplace = True)
yoga_cumul.tail(5)

Neighborhood Venue Category  Category Count  #Yoga Venues
454  India Bazaar    Event Space               1             1
455  India Bazaar          Greek               1             1
456  India Bazaar     Sandwiches               1             1
457  India Bazaar       Pharmacy               1             1
458     Guildwood   Martial Arts               1             1

<h2 style="color:blue;">3. <u>Data Analysis</u></h2>

In [32]:
# one hot encoding
yoga_onehot = pd.get_dummies(yoga_cumul[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
yoga_onehot['counts'] = yoga_cumul['counts'] 
yoga_onehot['Category Count'] = yoga_cumul['Category Count']


In [33]:
# set number of clusters
kclusters = 8

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(yoga_onehot)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([6, 6, 1, 1, 1, 1, 1, 1, 1, 1])

In [34]:
# add clustering labels
yoga_cumul.insert(0, 'Cluster Labels', kmeans.labels_)
yoga_cumul.head()

Cluster Labels Neighborhood      Venue Category  Category Count  counts
0               6  Regent Park         Coffee Shop              13      15
1               6  Regent Park          Sandwiches              10      15
2               1  Regent Park  Vegetarian / Vegan               7      15
3               1  Regent Park                Café               7      15
4               1  Regent Park             Apparel               6      15

In [35]:
yoga_cumul.head()

Cluster Labels Neighborhood      Venue Category  Category Count  counts
0               6  Regent Park         Coffee Shop              13      15
1               6  Regent Park          Sandwiches              10      15
2               1  Regent Park  Vegetarian / Vegan               7      15
3               1  Regent Park                Café               7      15
4               1  Regent Park             Apparel               6      15

In [36]:
#Merging the yoga_cumul with the neighborhood latitude and longitude data
yoga_cumul2 = yoga_cumul.merge(dfmerge)
yoga_cumul2.head()

Cluster Labels Neighborhood      Venue Category  Category Count  counts  \
0               6  Regent Park         Coffee Shop              13      15   
1               6  Regent Park          Sandwiches              10      15   
2               1  Regent Park  Vegetarian / Vegan               7      15   
3               1  Regent Park                Café               7      15   
4               1  Regent Park             Apparel               6      15   

  Postal Code           Borough  Latitude  Longitude  
0         M5A  Downtown Toronto  43.65426 -79.360636  
1         M5A  Downtown Toronto  43.65426 -79.360636  
2         M5A  Downtown Toronto  43.65426 -79.360636  
3         M5A  Downtown Toronto  43.65426 -79.360636  
4         M5A  Downtown Toronto  43.65426 -79.360636

In [37]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(yoga_cumul2['Latitude'], yoga_cumul2['Longitude'], yoga_cumul2['Neighborhood'], yoga_cumul2['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.9).add_to(map_clusters)
       
map_clusters

### Examine Clusters

Now, let's examine each cluster and determine the discriminating venue categories that distinguish each cluster. 

#### Cluster 1: Top near by venue is Vegetarian / Vegan place

In [38]:
yoga_cumul2.loc[yoga_cumul2['Cluster Labels'] == 0, yoga_cumul2.columns[[1] + list(range(2, yoga_cumul2.shape[1]))]]

Neighborhood           Venue Category  Category Count  counts  \
233  Parkview Hill               Restaurant               2       2   
234  Parkview Hill                  Italian               2       2   
235  Parkview Hill                Ice Cream               2       2   
236  Parkview Hill  Fruit & Vegetable Store               1       2   
237  Parkview Hill                Juice Bar               1       2   
..             ...                      ...             ...     ...   
490   India Bazaar              Event Space               1       1   
491   India Bazaar                    Greek               1       1   
492   India Bazaar               Sandwiches               1       1   
493   India Bazaar                 Pharmacy               1       1   
494      Guildwood             Martial Arts               1       1   

    Postal Code       Borough   Latitude  Longitude  
233         M4B     East York  43.706397 -79.309937  
234         M4B     East York  43.706397 -79.309937  
235         M4B     East York  43.706397 -79.309937  
236         M4B     East York  43.706397 -79.309937  
237         M4B     East York  43.706397 -79.309937  
..          ...           ...        ...        ...  
490         M4L  East Toronto  43.668999 -79.315572  
491         M4L  East Toronto  43.668999 -79.315572  
492         M4L  East Toronto  43.668999 -79.315572  
493         M4L  East Toronto  43.668999 -79.315572  
494         M1E   Scarborough  43.763573 -79.188711  

[155 rows x 8 columns]

#### Cluster 2: Top Venue is Restaurant

In [39]:
yoga_cumul2.loc[yoga_cumul2['Cluster Labels'] == 1, yoga_cumul2.columns[[1] + list(range(2, yoga_cumul2.shape[1]))]]

Neighborhood      Venue Category  Category Count  counts Postal Code  \
2   Regent Park  Vegetarian / Vegan               7      15         M5A   
3   Regent Park                Café               7      15         M5A   
4   Regent Park             Apparel               6      15         M5A   
5   Regent Park           Cosmetics               6      15         M5A   
6   Regent Park                Park               5      15         M5A   
7   Regent Park         Music Venue               5      15         M5A   
8   Regent Park            Japanese               5      15         M5A   
9   Regent Park             Italian               4      15         M5A   
10  Regent Park          Restaurant               4      15         M5A   
11  Regent Park               Diner               4      15         M5A   
12  Regent Park               Pizza               4      15         M5A   
13  Regent Park            Cocktail               4      15         M5A   
14  Regent Park           Bookstore               4      15         M5A   
15  Regent Park               Hotel               4      15         M5A   
16  Regent Park       Gym / Fitness               4      15         M5A   
17  Regent Park                 Gym               4      15         M5A   
18  Regent Park       Grocery Store               4      15         M5A   
19  Regent Park    Furniture / Home               4      15         M5A   
20  Regent Park           Breakfast               3      15         M5A   
21  Regent Park          Bubble Tea               3      15         M5A   
22  Regent Park    Department Store               3      15         M5A   
23  Regent Park              Bistro               3      15         M5A   
24  Regent Park             Theater               3      15         M5A   
25  Regent Park               Shoes               3      15         M5A   
26  Regent Park            Beer Bar               3      15         M5A   
27  Regent Park                 Bar               3      15         M5A   
28  Regent Park              Bakery               3      15         M5A   
29  Regent Park             Optical               3      15         M5A   
30  Regent Park            Creperie               3      15         M5A   
31  Regent Park           Ice Cream               3      15         M5A   
32  Regent Park              French               3      15         M5A   
33  Regent Park        Dance Studio               3      15         M5A   
34  Regent Park         Electronics               3      15         M5A   
35  Regent Park             Burgers               3      15         M5A   

             Borough  Latitude  Longitude  
2   Downtown Toronto  43.65426 -79.360636  
3   Downtown Toronto  43.65426 -79.360636  
4   Downtown Toronto  43.65426 -79.360636  
5   Downtown Toronto  43.65426 -79.360636  
6   Downtown Toronto  43.65426 -79.360636  
7   Downtown Toronto  43.65426 -79.360636  
8   Downtown Toronto  43.65426 -79.360636  
9   Downtown Toronto  43.65426 -79.360636  
10  Downtown Toronto  43.65426 -79.360636  
11  Downtown Toronto  43.65426 -79.360636  
12  Downtown Toronto  43.65426 -79.360636  
13  Downtown Toronto  43.65426 -79.360636  
14  Downtown Toronto  43.65426 -79.360636  
15  Downtown Toronto  43.65426 -79.360636  
16  Downtown Toronto  43.65426 -79.360636  
17  Downtown Toronto  43.65426 -79.360636  
18  Downtown Toronto  43.65426 -79.360636  
19  Downtown Toronto  43.65426 -79.360636  
20  Downtown Toronto  43.65426 -79.360636  
21  Downtown Toronto  43.65426 -79.360636  
22  Downtown Toronto  43.65426 -79.360636  
23  Downtown Toronto  43.65426 -79.360636  
24  Downtown Toronto  43.65426 -79.360636  
25  Downtown Toronto  43.65426 -79.360636  
26  Downtown Toronto  43.65426 -79.360636  
27  Downtown Toronto  43.65426 -79.360636  
28  Downtown Toronto  43.65426 -79.360636  
29  Downtown Toronto  43.65426 -79.360636  
30  Downtown Toronto  43.65426 -79.360636  
31  Downtown Toronto  43.65426 -79.360636  
32  Downtown 

#### Cluster 3

In [40]:
yoga_cumul2.loc[yoga_cumul2['Cluster Labels'] == 2, yoga_cumul2.columns[[1] + list(range(2, yoga_cumul2.shape[1]))]]

Neighborhood  Venue Category  Category Count  counts Postal Code  \
201  Woodbine Heights             Spa               2       3         M4C   
202  Woodbine Heights             Gym               2       3         M4C   
203  Woodbine Heights             BBQ               2       3         M4C   
204  Woodbine Heights          Lounge               1       3         M4C   
205  Woodbine Heights        Japanese               1       3         M4C   
..                ...             ...             ...     ...         ...   
383    Bathurst Manor             Pub               1       3         M3H   
384    Bathurst Manor  Middle Eastern               1       3         M3H   
385    Bathurst Manor          Korean               1       3         M3H   
386    Bathurst Manor       Fast Food               1       3         M3H   
387    Bathurst Manor  Discount Store               1       3         M3H   

        Borough   Latitude  Longitude  
201   East York  43.695344 -79.318389  
202   East York  43.695344 -79.318389  
203   East York  43.695344 -79.318389  
204   East York  43.695344 -79.318389  
205   East York  43.695344 -79.318389  
..          ...        ...        ...  
383  North York  43.754328 -79.442259  
384  North York  43.754328 -79.442259  
385  North York  43.754328 -79.442259  
386  North York  43.754328 -79.442259  
387  North York  43.754328 -79.442259  

[107 rows x 8 columns]

#### Cluster 4: Top Venue is a Fast Food joint

In [41]:
yoga_cumul2.loc[yoga_cumul2['Cluster Labels'] == 3, yoga_cumul2.columns[[1] + list(range(2, yoga_cumul2.shape[1]))]]

Neighborhood Venue Category  Category Count  counts Postal Code  \
113          Glencairn      Fast Food               3       6         M6B   
114          Glencairn            Gym               3       6         M6B   
115          Glencairn           Thai               2       6         M6B   
116          Glencairn          Ramen               2       6         M6B   
117          Glencairn            Pub               2       6         M6B   
..                 ...            ...             ...     ...         ...   
401  Hillcrest Village        Dim Sum               1       5         M2H   
402  Hillcrest Village    Coffee Shop               1       5         M2H   
403  Hillcrest Village     Bubble Tea               1       5         M2H   
404  Hillcrest Village            Bar               1       5         M2H   
405  Hillcrest Village         Bakery               1       5         M2H   

        Borough   Latitude  Longitude  
113  North York  43.709577 -79.445073  
114  North York  43.709577 -79.445073  
115  North York  43.709577 -79.445073  
116  North York  43.709577 -79.445073  
117  North York  43.709577 -79.445073  
..          ...        ...        ...  
401  North York  43.803762 -79.363452  
402  North York  43.803762 -79.363452  
403  North York  43.803762 -79.363452  
404  North York  43.803762 -79.363452  
405  North York  43.803762 -79.363452  

[101 rows x 8 columns]

#### Cluster 5

In [42]:
yoga_cumul2.loc[yoga_cumul2['Cluster Labels'] == 4, yoga_cumul2.columns[[1] + list(range(2, yoga_cumul2.shape[1]))]]

Neighborhood      Venue Category  Category Count  counts Postal Code  \
36   Regent Park       Movie Theater               2      15         M5A   
37   Regent Park      Middle Eastern               2      15         M5A   
38   Regent Park             Mexican               2      15         M5A   
39   Regent Park             Seafood               2      15         M5A   
40   Regent Park                 Spa               2      15         M5A   
..           ...                 ...             ...     ...         ...   
101  Regent Park  Salon / Barbershop               1      15         M5A   
102  Regent Park             Brewery               1      15         M5A   
103  Regent Park            Baseball               1      15         M5A   
104  Regent Park              Arepas               1      15         M5A   
105  Regent Park         Accessories               1      15         M5A   

              Borough  Latitude  Longitude  
36   Downtown Toronto  43.65426 -79.360636  
37   Downtown Toronto  43.65426 -79.360636  
38   Downtown Toronto  43.65426 -79.360636  
39   Downtown Toronto  43.65426 -79.360636  
40   Downtown Toronto  43.65426 -79.360636  
..                ...       ...        ...  
101  Downtown Toronto  43.65426 -79.360636  
102  Downtown Toronto  43.65426 -79.360636  
103  Downtown Toronto  43.65426 -79.360636  
104  Downtown Toronto  43.65426 -79.360636  
105  Downtown Toronto  43.65426 -79.360636  

[70 rows x 8 columns]

#### Cluster 6: Top venue is Coffee Shop

In [43]:
yoga_cumul2.loc[yoga_cumul2['Cluster Labels'] == 5, yoga_cumul2.columns[[1] + list(range(2, yoga_cumul2.shape[1]))]]

Neighborhood Venue Category  Category Count  counts Postal Code  \
106         Glencairn    Coffee Shop              10       6         M6B   
107         Glencairn           Café               6       6         M6B   
108         Glencairn     Restaurant               5       6         M6B   
109         Glencairn        Mexican               4       6         M6B   
110         Glencairn        Italian               4       6         M6B   
111         Glencairn          Sushi               4       6         M6B   
112         Glencairn         Bakery               4       6         M6B   
165  Islington Avenue    Coffee Shop               9       5         M9A   
166  Islington Avenue          Pizza               5       5         M9A   
167  Islington Avenue            Pub               5       5         M9A   

        Borough   Latitude  Longitude  
106  North York  43.709577 -79.445073  
107  North York  43.709577 -79.445073  
108  North York  43.709577 -79.445073  
109  North York  43.709577 -79.445073  
110  North York  43.709577 -79.445073  
111  North York  43.709577 -79.445073  
112  North York  43.709577 -79.445073  
165   Etobicoke  43.667856 -79.532242  
166   Etobicoke  43.667856 -79.532242  
167   Etobicoke  43.667856 -79.532242

#### Cluster 7: Top venue is Coffee Shop

In [44]:
yoga_cumul2.loc[yoga_cumul2['Cluster Labels'] == 6, yoga_cumul2.columns[[1] + list(range(2, yoga_cumul2.shape[1]))]]

Neighborhood Venue Category  Category Count  counts Postal Code  \
0  Regent Park    Coffee Shop              13      15         M5A   
1  Regent Park     Sandwiches              10      15         M5A   

            Borough  Latitude  Longitude  
0  Downtown Toronto  43.65426 -79.360636  
1  Downtown Toronto  43.65426 -79.360636

#### Cluster 8: Top Venue Category is Pub

In [45]:
yoga_cumul2.loc[yoga_cumul2['Cluster Labels'] == 7, yoga_cumul2.columns[[1] + list(range(2, yoga_cumul2.shape[1]))]]

Neighborhood Venue Category  Category Count  counts Postal Code  \
199    Woodbine Heights            Pub               5       3         M4C   
200    Woodbine Heights    Coffee Shop               3       3         M4C   
232       Parkview Hill          Greek               5       2         M4B   
251              Woburn        Apparel               5       1         M1G   
267   Banbury-Don Mills    Coffee Shop               4       3         M3B   
289  Caledonia-Fairbank            Bar               4       3         M6E   
290  Caledonia-Fairbank        Italian               3       3         M6E   
291  Caledonia-Fairbank  Grocery Store               3       3         M6E   
322           Runnymede          Pizza               3       2         M6N   
323           Runnymede          Pizza               3       2         M6S   
324           Runnymede    Coffee Shop               3       2         M6N   
325           Runnymede    Coffee Shop               3       2         M6S   
350          Rouge Hill            Pub               3       2         M1C   
360      Bathurst Manor     Restaurant               3       3         M3H   
361      Bathurst Manor       Japanese               3       3         M3H   
362      Bathurst Manor    Coffee Shop               3       3         M3H   

          Borough   Latitude  Longitude  
199     East York  43.695344 -79.318389  
200     East York  43.695344 -79.318389  
232     East York  43.706397 -79.309937  
251   Scarborough  43.770992 -79.216917  
267    North York  43.745906 -79.352188  
289          York  43.689026 -79.453512  
290          York  43.689026 -79.453512  
291          York  43.689026 -79.453512  
322          York  43.673185 -79.487262  
323  West Toronto  43.651571 -79.484450  
324          York  43.673185 -79.487262  
325  West Toronto  43.651571 -79.484450  
350   Scarborough  43.784535 -79.160497  
360    North York  43.754328 -79.442259  
361    North York  43.754328 -79.442259  
362    North York  43.754328 -79.442259

<h2 style="color:blue;">4. <u>Results</u></h2
    

### Based on the data, the Regent Park neighborhood has the highest # of yoga studios.

In [ ]:
countbyneigh.head()

In [ ]:
countbyneigh.set_index(['Neighborhood'], inplace = True)


In [ ]:
# step 2: plot data
countbyneigh.plot(kind='bar', 
                  color='#5cb85c',
                  figsize=(15, 9))

plt.xlabel('Neighborhood') 
plt.ylabel('Number of Yoga Studios') 
plt.title('Number of Yoga Studios by Neighborhood') 

plt.show()

### Many Yoga Studios are surrounded by Coffee Shops

In [ ]:
byvenue = surrounding_venues.drop(['Neighborhood','Yoga Place','Yoga Place Latitude','Yoga Place Longitude','Venue','Venue Latitude','Venue Longitude' ], axis = 1)
byvenue= byvenue.groupby(['Venue Category']).size().reset_index(name='Total Venues')

In [ ]:
byvenue = byvenue.sort_values(['Total Venues'], ascending = False,ignore_index=True)
byvenue = byvenue.set_index(['Venue Category'])

In [ ]:
byvenue.head(7)

In [ ]:
# step 2: plot data
byvenue.head(10).plot(kind='bar',
                      color='#5bc0de',
                  figsize=(15, 10))

plt.xlabel('Venue Category') 
plt.ylabel('Venue Count') 
plt.title('Top 10 venues surrounding yoga studios') 

plt.show()

Thank you for reviewing my notebook! :) - All discussions and conclusions are in my report and presentation